# Notebook 2: Application d'analyse immobilière
---
## Table des matières

1. [Présentation du projet](#Présentation-du-projet)
2. [Objectifs de l'application](#Objectifs-de-l'application)
3. [Sources de données](#Sources-de-données)
4. [Import des bibliothèques](#Import-des-bibliothèques)
5. [Chargement des données](#Chargement-des-données)
6. [Vue d'ensemble du marché](#Vue-d'ensemble-du-marché)
7. [Exploration interactive par budget](#Exploration-interactive-par-budget)
8. [Analyse géographique](#Analyse-géographique)
9. [Système de recommandation](#Système-de-recommandation)
10. [Analyse prédictive](#Analyse-prédictive)
11. [Tableaux de bord personnalisés](#Tableaux-de-bord-personnalisés)
12. [Conclusions et recommandations](#Conclusions-et-recommandations)
13. [Annexes](#Annexes)
14. [Guide d'utilisation](#Guide-d'utilisation)

---

## Présentation du projet
### Persona ciblé

#### Profil
**Nom**: Marie
**Age**: 40 ans
**Occupation**: cadre supérieur à Paris

**Budget**: 300-500k€

**Objectif**: Acheter son premier bien locatif pour générer des revenus passifs


#### Besoins spécifiques
1. Identifier les villes avec le meilleur rendement locatif dans IDF
2. Comprendre quels types de biens sont les plus rentables (studio vs T3 pour coloc)
3. Calculer la rentabilité brute et nette
4. Comparer le potentiel de location simple vs coloc
5. Analyser les proximité des transport en commun
6. Trouver des biens accessibles avec son budget
7. Avoir un aperçu clair du marché (prix au m2,tendances)
8. Observer l’évolution des prix sur 5–10 ans pour anticiper une plus-value
9. Évaluer la liquidité du marché
10. Obtenir un classement des Top 10 opportunités actuelles (un tableau ou score automatique).
11. Analyser les charges moyennes par type de logement
12. Vérifier la sécurité et l’attractivité du quartier


---

## Objectifs de l'application
<!-- COMPLÉTEZ ICI: Listez les objectifs principaux de votre application -->
<!-- Exemple: -->
<!-- - Identifier les zones à fort potentiel de rentabilité -->
<!-- - Calculer le ROI d'un investissement immobilier -->
<!-- - etc. -->
Identifier des territoires prometteurs pour un premier investissement locatif

---

## Sources de données
<!-- COMPLÉTEZ ICI: Décrivez vos sources de données -->
<!-- - Données principales (DVF, etc.) -->
<!-- - Données complémentaires (INSEE, API, etc.) -->
<!-- - Période couverte -->
<!-- - Nombre de transactions analysées -->

---

## Import des bibliothèques

In [ ]:
# Importation des bibliothèques nécessaires
import pandas as pd
import numpy as np
import seaborn as sns

# Pour les visualisations interactives
import plotly.express as px
import plotly.graph_objects as go 
import ipywidgets as widgets
import matplotlib.pyplot as plt

import folium
import geopandas as gpd
from folium.plugins import MarkerCluster

# CODEZ ICI: Configuration supplémentaire si nécessaire

---

## Chargement des données

In [ ]:
# --- Chargement des données nettoyées (préparées dans le Notebook 1) ---
# Indicateurs de loyer
df = pd.read_csv('data/cleaned/loyers_IDF_2024.csv')

# Transports
transports_gdf = gpd.read_file("data/transports_nettoyes.geojson")

---

## Vue d'ensemble du marché

### Widget 1.1 : Statistiques globales (simple/statique)
<!-- COMPLÉTEZ ICI: Décrivez ce que ce widget doit montrer -->
<!-- Exemple: Nombre total de transactions, prix moyen national, etc. -->


In [ ]:
def nature_transaction(df):
    """Affiche la distribution des types de transactions du marché immobilier."""
    nature_mutation_counts = df["nature_mutation"].value_counts().reset_index()
    nature_mutation_counts.columns = ['Nature', 'Count']

    fig = px.bar(nature_mutation_counts,
                 x='Nature', 
                 y='Count',
                 title='Distribution des types de transactions',
                 text='Count')
    
    fig.show()
    return

nature_transaction(df)


### Widget 1.2 
<!-- COMPLÉTEZ ICI: Décrivez la visualisation attendue -->
<!-- Exemple: Graphique linéaire montrant l'évolution des prix moyens par année -->


In [ ]:
def prix_moyen_par_type(df):
    """Afficher le prix moyen par type de bien immobilier."""
    avg_price_by_type = df.groupby("type_local")["valeur_fonciere"].mean().reset_index()
    # print(avg_price_by_type)
    print(avg_price_by_type.dtypes)
    avg_price_by_type.columns = ["Type", "Avg price"]

    fig = px.bar(avg_price_by_type,
                 x="Type",
                 y="Avg price",
                 title="Prix moyen par type de bien immobilier",
                 text="Avg price")
    fig.update_traces(
        texttemplate='%{text:.2f} €',
        hovertemplate='Type: %{x}<br>Prix moyen: %{y:.2f} €'
    )
    fig.show()

prix_moyen_par_type(df)

### Widget 1.3
<!-- COMPLÉTEZ ICI: Décrivez le type de graphique et les insights attendus -->


In [ ]:
# Distribution par département
def distribution_par_departement(df, sort=False):
    df['code_departement'] = df['code_departement'].astype(str)
    
    # Filter departments where numeric code is less than 100
    df_filtered = df[pd.to_numeric(df['code_departement'], errors='coerce') < 100]
    
    dept_counts = df_filtered['code_departement'].value_counts(sort=sort).reset_index()
    dept_counts.columns = ['Département', 'Count']
    
    # Department names mapping
    dept_names = {
        '01': 'Ain', '02': 'Aisne', '03': 'Allier', '04': 'Alpes-de-Haute-Provence',
        '05': 'Hautes-Alpes', '06': 'Alpes-Maritimes', '07': 'Ardèche', '08': 'Ardennes',
        '09': 'Ariège', '10': 'Aube', '11': 'Aude', '12': 'Aveyron',
        '13': 'Bouches-du-Rhône', '14': 'Calvados', '15': 'Cantal', '16': 'Charente',
        '17': 'Charente-Maritime', '18': 'Cher', '19': 'Corrèze', '21': "Côte-d'Or",
        '22': "Côtes-d'Armor", '23': 'Creuse', '24': 'Dordogne', '25': 'Doubs',
        '26': 'Drôme', '27': 'Eure', '28': 'Eure-et-Loir', '29': 'Finistère',
        '2A': 'Corse-du-Sud', '2B': 'Haute-Corse', '30': 'Gard', '31': 'Haute-Garonne',
        '32': 'Gers', '33': 'Gironde', '34': 'Hérault', '35': 'Ille-et-Vilaine',
        '36': 'Indre', '37': 'Indre-et-Loire', '38': 'Isère', '39': 'Jura',
        '40': 'Landes', '41': 'Loir-et-Cher', '42': 'Loire', '43': 'Haute-Loire',
        '44': 'Loire-Atlantique', '45': 'Loiret', '46': 'Lot', '47': 'Lot-et-Garonne',
        '48': 'Lozère', '49': 'Maine-et-Loire', '50': 'Manche', '51': 'Marne',
        '52': 'Haute-Marne', '53': 'Mayenne', '54': 'Meurthe-et-Moselle', '55': 'Meuse',
        '56': 'Morbihan', '57': 'Moselle', '58': 'Nièvre', '59': 'Nord',
        '60': 'Oise', '61': 'Orne', '62': 'Pas-de-Calais', '63': 'Puy-de-Dôme',
        '64': 'Pyrénées-Atlantiques', '65': 'Hautes-Pyrénées', '66': 'Pyrénées-Orientales',
        '67': 'Bas-Rhin', '68': 'Haut-Rhin', '69': 'Rhône', '70': 'Haute-Saône',
        '71': 'Saône-et-Loire', '72': 'Sarthe', '73': 'Savoie', '74': 'Haute-Savoie',
        '75': 'Paris', '76': 'Seine-Maritime', '77': 'Seine-et-Marne', '78': 'Yvelines',
        '79': 'Deux-Sèvres', '80': 'Somme', '81': 'Tarn', '82': 'Tarn-et-Garonne',
        '83': 'Var', '84': 'Vaucluse', '85': 'Vendée', '86': 'Vienne',
        '87': 'Haute-Vienne', '88': 'Vosges', '89': 'Yonne', '90': 'Territoire de Belfort',
        '91': 'Essonne', '92': 'Hauts-de-Seine', '93': 'Seine-Saint-Denis', '94': 'Val-de-Marne',
        '95': "Val-d'Oise"
    }
    
    # Ensure Département column is string type
    dept_counts['Département'] = dept_counts['Département'].astype(str)
    dept_counts['Nom'] = dept_counts['Département'].map(dept_names)
    
    fig = px.bar(dept_counts,
                 x='Département',
                 y='Count',
                 title='Distribution par département (code < 100)',
                 text='Count',
                 hover_data=['Nom'])
    fig.show()

distribution_par_departement(df, sort=True)

## Exploration interactive par budget

### Widget 2.1 : Explorateur de budget (interactif - 1 à 3 paramètres)
<!-- COMPLÉTEZ ICI: Décrivez les paramètres interactifs -->
<!-- Exemple: -->
<!-- - Slider pour le budget (min-max) -->
<!-- - Menu déroulant pour le type de bien -->
<!-- - Slider pour la surface minimale -->

In [ ]:
# CODEZ ICI: Créer les widgets interactifs (sliders, dropdowns, etc.)

# CODEZ ICI: Fonction de filtrage basée sur les paramètres

# CODEZ ICI: Affichage des résultats (tableau + graphique)

### Widget 2.2 : Calculateur de rentabilité locative (interactif - 1 à 3 paramètres)
<!-- COMPLÉTEZ ICI: Décrivez les paramètres -->
<!-- Exemple: Prix d'achat, loyer mensuel estimé, charges, etc. -->


In [ ]:
# CODEZ ICI: Créer les inputs interactifs

# CODEZ ICI: Fonction de calcul du ROI, rendement brut, rendement net

# CODEZ ICI: Affichage des résultats avec visualisation

---

## Analyse géographique

### Widget 3.1 : Carte intéractive (fltre budget + valeures foncières)

<!-- COMPLÉTEZ ICI: Décrivez la comparaison attendue -->
<!-- Exemple: Comparer 2-3 régions/villes sur plusieurs critères -->


In [ ]:
import folium
import pandas as pd
import geopandas as gpd
from folium.plugins import MarkerCluster
import ipywidgets as widgets
from IPython.display import display, clear_output, HTML
import branca.colormap as cm

# === 1. Chargement des fichiers ===
communes_gdf = gpd.read_file("data/communes_coordonnees.geojson")

# === 2. Chargement du fichier DVF (valeurs foncières) ===
dvf_df = pd.read_csv("data/cleaned/dvf_idf_clean.csv")

# Conversion de la colonne valeur_fonciere en nombre
dvf_df["valeur_fonciere"] = pd.to_numeric(dvf_df["valeur_fonciere"], errors="coerce")

# Assurer que les codes communaux sont des chaînes pour la jointure
dvf_df["code_commune"] = dvf_df["code_commune"].astype(str)
communes_gdf["INSEE_COM"] = communes_gdf["INSEE_COM"].astype(str)

# === 3. Calcul de la moyenne par commune ===
moyennes_df = (
    dvf_df.groupby(["code_commune", "nom_commune"], as_index=False)["valeur_fonciere"]
    .mean()
    .rename(columns={"valeur_fonciere": "valeur_fonciere_moyenne"})
)

# Fusion sur les codes INSEE
communes_valeurs = communes_gdf.merge(
    moyennes_df, left_on="INSEE_COM", right_on="code_commune", how="inner"
)

# === 4. Palette dynamique ===
min_val = communes_valeurs["valeur_fonciere_moyenne"].min()
max_val = communes_valeurs["valeur_fonciere_moyenne"].max()
colormap = cm.linear.YlOrRd_09.scale(min_val, max_val)
colormap.caption = "Valeur foncière moyenne (€)"

# === 5. Fonction d'affichage de la carte ===
def afficher_carte_range(budget_range):
    budget_min, budget_max = budget_range

    clear_output(wait=True)  # Nettoie l'affichage à chaque interaction

    # Filtrer selon la fourchette
    communes_filtrees = communes_valeurs[
        (communes_valeurs["valeur_fonciere_moyenne"] >= budget_min)
        & (communes_valeurs["valeur_fonciere_moyenne"] <= budget_max)
    ]

    # Créer la carte
    m = folium.Map(location=[48.8566, 2.3522], zoom_start=9, tiles="CartoDB positron")
    cluster = MarkerCluster(name=f"Entre {budget_min:,.0f} € et {budget_max:,.0f} €").add_to(m)

    # Ajouter les points filtrés
    for _, row in communes_filtrees.iterrows():
        valeur = row["valeur_fonciere_moyenne"]
        commune = row["nom_commune"]
        coords = (row.geometry.y, row.geometry.x)
        color = colormap(valeur)

        popup = f"""
        <div style="
            font-family: Arial, sans-serif;
            font-size: 13px;
            line-height: 1.5;
            border-radius: 10px;
            padding: 10px 15px;
            background-color: rgba(255,255,255,0.95);
            box-shadow: 0 2px 8px rgba(0,0,0,0.2);
            min-width: 160px;
            text-align: center;
        ">
            <h4 style="margin:0; color:{color}; font-size:15px;">
                🏙️ <b>{commune}</b>
            </h4>
            <hr style="border:none; border-top:1px solid #ddd; margin:6px 0;">
            <p style="margin:3px 0; font-size:13px;">
                💰 <b>Valeur foncière moyenne :</b><br>
                <span style="color:{color}; font-weight:bold; font-size:14px;">{valeur:,.0f} €</span>
            </p>
        </div>
        """

        folium.CircleMarker(
            location=coords,
            radius=5,
            color=color,
            fill=True,
            fill_color=color,
            fill_opacity=0.8,
            popup=popup
        ).add_to(cluster)

    # Ajouter la légende
    colormap.add_to(m)
    display(m)

# === 6. Slider interactif ===
range_slider = widgets.IntRangeSlider(
    value=(int(min_val), int(max_val/2)),
    min=int(min_val),
    max=int(max_val),
    step=50000,
    description='📊 Budget (min - max)',
    continuous_update=False,
    layout=widgets.Layout(width="75%"),
    style={'description_width': 'initial'}
)

# === 7. Connexion interactive propre (sans doublons) ===
out = widgets.interactive_output(afficher_carte_range, {'budget_range': range_slider})

# === 8. Affichage soigné ===
from IPython.display import HTML, display

style_html = """
<style>

/* Texte du budget sélectionné */
.output_subarea {
    color: #FFFFFF !important;
    font-family: 'Segoe UI', sans-serif;
    font-size: 14px;
}

/* Zone du slider */
.widget-inline-hbox {
    background-color: #6C8AA5 !important;
    border-radius: 12px;
    padding: 10px 20px;
    box-shadow: 0 2px 6px rgba(0,0,0,0.6);
}

</style>
"""

display(HTML(style_html))
display(range_slider, out)


IntRangeSlider(value=(60000, 715000), continuous_update=False, description='📊 Budget (min - max)', layout=Layo…

Output()

### Widget 3.2 : Carte intéractive (transports + valeures foncières)

<!-- COMPLÉTEZ ICI: Décrivez les fonctionnalités de la carte -->
<!-- Exemple: -->
<!-- - Carte choroplèthe des prix moyens -->
<!-- - Filtres par type de bien -->
<!-- - Pop-up avec détails au clic -->
<!-- - Layers pour différentes métriques -->

In [4]:
import folium
import pandas as pd
import geopandas as gpd
from folium.plugins import MarkerCluster
import branca.colormap as cm

# === 1. Chargement des fichiers ===
transports_gdf = gpd.read_file("data/transports_nettoyes.geojson")
communes_gdf = gpd.read_file("data/communes_coordonnees.geojson")

# === 2. Chargement du fichier DVF (valeurs foncières) ===
dvf_df = pd.read_csv("data/cleaned/dvf_idf_clean.csv")

# Conversion de la colonne valeur_fonciere en nombre
dvf_df["valeur_fonciere"] = pd.to_numeric(dvf_df["valeur_fonciere"], errors="coerce")

# Assurer que les codes communaux sont des chaînes pour la jointure
dvf_df["code_commune"] = dvf_df["code_commune"].astype(str)
communes_gdf["INSEE_COM"] = communes_gdf["INSEE_COM"].astype(str)

# === 3. Calcul de la moyenne par commune ===
moyennes_df = (
    dvf_df.groupby(["code_commune", "nom_commune"], as_index=False)["valeur_fonciere"]
    .mean()
    .rename(columns={"valeur_fonciere": "valeur_fonciere_moyenne"})
)

# Fusion sur les codes INSEE
communes_valeurs = communes_gdf.merge(
    moyennes_df, left_on="INSEE_COM", right_on="code_commune", how="inner"
)

# === 4. Création de la carte ===
m = folium.Map(location=[48.8566, 2.3522], zoom_start=9, tiles="CartoDB positron")


# === 6. Ajout des gares/transports ===
for t in transports_gdf["type"].unique():
    subset = transports_gdf[transports_gdf["type"] == t]
    cluster_type = MarkerCluster(name=f"{t}").add_to(m)


    for _, row in subset.iterrows():
        picto = row["picto_url"]
        popup_html = f"""
        <div style='font-size:13px; line-height:1.4'>
            <b>{row['nom']}</b><br>
            🚈 Type : {t}<br>
            🧭 Ligne : {row['ligne']}<br>
            🏢 Exploitant : {row['exploitant']}<br>
            <img src="{picto}" width="50"><br>
            <i>Coordonnées : {round(row.geometry.x, 3)}, {round(row.geometry.y, 3)}</i>
        </div>
        """
        try:
            icon = folium.CustomIcon(icon_image=picto, icon_size=(30, 30), icon_anchor=(15, 15))
            folium.Marker(
                location=[row.geometry.y, row.geometry.x],
                popup=folium.Popup(popup_html, max_width=300),
                icon=icon
            ).add_to(cluster_type)
        except Exception as e:
            print(f"⚠️ Erreur sur {row['nom']}: {e}")

# === 7. Ajout des valeurs foncières moyennes par commune ===
min_val = communes_valeurs["valeur_fonciere_moyenne"].min()
max_val = communes_valeurs["valeur_fonciere_moyenne"].max()

colormap = cm.LinearColormap(
    colors=["#F5E6CC", "#A9C5D3", "#3B6EA5"],  # beige clair → bleu ciel → bleu profond
    vmin=min_val,
    vmax=max_val,
    caption="Valeur foncière moyenne (€)"
)


for _, row in communes_valeurs.iterrows():
    valeur = row["valeur_fonciere_moyenne"]
    commune = row["nom_commune"]
    coords = (row.geometry.y, row.geometry.x)

    if pd.isna(valeur):
        continue

    # Couleur issue du colormap dynamique
    color = colormap(valeur)

    popup = f"""
    <div style="
        font-family: Arial, sans-serif;
        font-size: 13px;
        line-height: 1.5;
        border-radius: 10px;
        padding: 10px 15px;
        background-color: rgba(255,255,255,0.95);
        box-shadow: 0 2px 8px rgba(0,0,0,0.2);
        min-width: 160px;
        text-align: center;
    ">
        <h4 style="margin:0; color:{color}; font-size:15px;">
            🏙️ <b>{commune}</b>
        </h4>
        <hr style="border:none; border-top:1px solid #ddd; margin:6px 0;">
        <p style="margin:3px 0; font-size:13px;">
            💰 <b>Valeur foncière moyenne :</b><br>
            <span style="color:{color}; font-weight:bold; font-size:14px;">{valeur:,.0f} €</span>
        </p>
    </div>
    """
    folium.CircleMarker(
        location=coords,
        radius=5,
        color=color,
        fill=True,
        fill_color=color,
        fill_opacity=0.7,
        popup=popup
    ).add_to(m)

# === 8. Barre de légende stylisée mais synchronisée avec le colormap ===
colormap.caption = "Valeur foncière moyenne (€)"
colormap.add_to(m)

# === 9. Contrôle des couches avec titre "Transports" ===
folium.LayerControl(collapsed=False).add_to(m)

# === 10. Personnalisation CSS ===
custom_html = """
<style>

/* Ciblage du LayerControl */
.leaflet-control-layers {
    position: fixed !important;
    bottom: 40px !important;
    left: 20px !important;
    right: auto !important;
    top: auto !important;
    z-index: 9999 !important;

    background: rgba(255, 255, 255, 0.95) !important;
    border: 1px solid #ccc !important;
    border-radius: 10px !important;
    box-shadow: 0 3px 8px rgba(0,0,0,0.25);
    font-family: "Segoe UI", Arial, sans-serif;
    font-size: 13.5px;
    padding: 6px 8px;
}

/* Masquer la base (cartodbpositron) */
.leaflet-control-layers-base {
    display: none !important;
}

/* Supprimer la barre grise séparatrice */
.leaflet-control-layers-separator {
    display: none !important;
}

/* Couleur des cases cochées et du bouton radio */
.leaflet-control-layers-selector {
    accent-color: #6C8AA5 !important;  /* gris bleuté élégant */
}
</style>
"""
m.get_root().html.add_child(folium.Element(custom_html))

# === 11. Sauvegarde ===
m.save("data/carte_transports_valeur_fonciere.html")
print("✅ Carte enregistrée : data/carte_transports_valeur_fonciere.html")
m


✅ Carte enregistrée : data/carte_transports_valeur_fonciere.html


### Widget 3.3 : Carte interactive 

---

## Système de recommandation

### Widget 4.1 : Détecteur d'opportunités (complexe - plus de 3 paramètres)

<!-- COMPLÉTEZ ICI: Décrivez tous les paramètres du système de recommandation -->
<!-- Exemple: -->
<!-- - Budget min/max -->
<!-- - Type(s) de bien souhaité(s) -->
<!-- - Rendement minimum attendu -->
<!-- - Région(s) préférée(s) -->
<!-- - Niveau de risque acceptable -->
<!-- - etc. -->

In [ ]:
# CODEZ ICI: Créer tous les widgets de paramétrage

# CODEZ ICI: Fonction de scoring/recommandation

# CODEZ ICI: Affichage des Top N opportunités recommandées

# CODEZ ICI: Visualisation des recommandations (tableau + carte/graphique)

---

## Tableaux de bord personnalisés

### Widget 6.1 : Dashboard personnalisé

<!-- COMPLÉTEZ ICI: Décrivez les éléments du dashboard -->
<!-- Un dashboard qui combine plusieurs métriques importantes pour le persona -->


In [ ]:
# CODEZ ICI: Créer un dashboard multi-graphiques

# CODEZ ICI: Possibilité de personnaliser les métriques affichées

---

## Conclusions et recommandations

### Synthèse des analyses
<!-- COMPLÉTEZ ICI: Rédigez les conclusions principales -->
<!-- Basées sur les analyses effectuées dans les sections précédentes -->

### Recommandations pour l'investisseur
<!-- COMPLÉTEZ ICI: Listez les recommandations concrètes -->
<!-- Exemple: -->
<!-- 1. Les 3 meilleures zones identifiées -->
<!-- 2. Le type de bien optimal -->
<!-- 3. Les zones à éviter -->
<!-- 4. Conseils stratégiques -->

### Points d'attention
<!-- COMPLÉTEZ ICI: Listez les limites et précautions -->
<!-- Exemple: Limites des données, facteurs non pris en compte, etc. -->

---

## Annexes

### Méthodologie
<!-- COMPLÉTEZ ICI: Expliquez votre méthodologie -->
<!-- - Comment les données ont été nettoyées -->
<!-- - Formules de calcul utilisées -->
<!-- - Choix techniques justifiés -->

### Sources et références
<!-- COMPLÉTEZ ICI: Listez toutes vos sources -->
<!-- - Liens vers les datasets -->
<!-- - Documentation des APIs utilisées -->
<!-- - Références bibliographiques si applicable -->

---

## Guide d'utilisation

### Comment utiliser ce notebook
<!-- COMPLÉTEZ ICI: Instructions pour l'utilisateur final -->
<!-- 1. Exécuter les cellules dans l'ordre -->
<!-- 2. Comment interagir avec les widgets -->
<!-- 3. Comment interpréter les résultats -->
<!-- etc. -->

### Dépendances requises

In [ ]:
# Liste des bibliothèques nécessaires
# COMPLÉTEZ ICI: Listez toutes les bibliothèques et leurs versions
# pandas==X.X.X
# matplotlib==X.X.X
# etc.

---

**Projet développé par :**
- Ashley OHNONA
- Harisoa RANDRIANASOLO
- Fairouz YOUDARENE
- Jennifer ZAHORA

**Date :** <!-- COMPLÉTEZ ICI: Date -->

**Version :** 1.0